In [91]:
%matplotlib inline
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import pandas as pd
import plotly.express as px
import zipfile
!pip -q install itables
from itables import init_notebook_mode
init_notebook_mode(all_interactive=True)
import itables.options as opt
opt.maxBytes = 0
opt.classes = ["display", "nowrap","compact","hover"]
opt.showIndex = False
opt.style = "max-width:6000px"
pd.set_option('display.max_colwidth', 20)

#set option to not use coeluting matches

<IPython.core.display.Javascript object>

This notebook provides a detailed analysis of one or more samples at the peptide, modification and protein level.

For each sample, the `ionbot.twbx` result file needs to be put into a seperate folder with the folder name corresponding to a unique sample name.  

We will analyse the ionbot search results of two samples and created one folder for each sample:

```
PXD000561
├── PXD000561_closed
│   └── ionbot.twbx
├── PXD000561_full
│   └── ionbot.twbx
├── PXD000561_nocorr_nort
│   └── ionbot.twbx
```

We can specify this as follows:

In [92]:
experiment = "PXD000561"
samples = ["PXD000561_closed","PXD000561_full","PXD000561_nocorr_nort"] 

In [93]:
for sample in samples:
    folder = "%s/%s/"%(experiment,sample)
    archive = zipfile.ZipFile("%s/ionbot.twbx"%folder)
    for file in archive.namelist():
        if file.startswith('Data/'):
            archive.extract(file, folder)

In [110]:
sample = "PXD000561_full"
folder = "%s/%s/Data/ionbot_result/"%(experiment,sample)
ionbot_first = pd.read_csv("%s/ionbot.first.csv"%folder)
ionbot_first["rank"] = ["first"]*len(ionbot_first)
ionbot_lower = pd.read_csv("%s/ionbot.lower.csv"%folder)
ionbot_lower["rank"] = ["lower"]*len(ionbot_lower)
ionbot = pd.concat([ionbot_first,ionbot_lower])
ionbot = ionbot[(ionbot["database"]=="T")&(ionbot["q-value"]<=0.01)]
ionbot["unexpected_modification"].fillna("-",inplace=True)
ionbot = ionbot[ionbot["unexpected_modification"]!="-"]
ionbot["prot"] = ionbot["proteins"].apply(lambda x: x.split("((")[0])
tmp = ionbot.drop_duplicates(["matched_peptide","unexpected_modification"])["prot"].value_counts().reset_index(level=0)
tmp.columns = ["proteins","#peptidoforms"]
tmp

proteins  #peptidoforms
0      MYH9_HUMAN            701
1      AHNK_HUMAN            619
2        H4_HUMAN            508
3      ACTG_HUMAN            483
4      K2C1_HUMAN            388
...           ...            ...
5006   K2C3_HUMAN              1
5007  GLT17_HUMAN              1
5008   WDR6_HUMAN              1
5009   UBR2_HUMAN              1
5010  ARL5B_HUMAN              1

[5011 rows x 2 columns]

In [119]:
tmp2 = ionbot[ionbot["prot"]=="TRYP_PIG"]
tmp2.drop_duplicates("unexpected_modification")
tmp2[["matched_peptide","modifications","unexpected_modification","proteins"]].to_csv("TRYP_PIG.csv",index=False)

In [116]:
tmp2 = ionbot[ionbot["proteins"]=="ACTG_HUMAN((148-178))((P63261))||ACTB_HUMAN((148-178))((P60709))"].to_csv("ACTG_HUMAN_TTGIVMDSGDGVTHTVPIYEGYAIPHAIIR.csv",index=False)

In [115]:
tmp2[["ionbot_match_id","matched_peptide","modifications","unexpected_modification"]].drop_duplicates("modifications")

In [95]:
proteins.head(100)

ionbot_match_id  is_shared_peptide protein_group  protein_group_q-value  \
0           22_5_1              False    B2MG_HUMAN                  0.0     
1           19_5_2              False     H13_HUMAN                  0.0     
2            0_1_3               True    K2C1_HUMAN                  0.0     
3            0_1_3               True    K2C1_HUMAN                  0.0     
4            0_1_3               True     sp|P04264                  0.0     
..             ...                ...           ...                  ...     
95       22_8386_3               True   1433E_HUMAN                  0.0     
96       22_8386_3               True   1433T_HUMAN                  0.0     
97       22_8386_3               True   1433Z_HUMAN                  0.0     
98       22_8386_3               True   1433F_HUMAN                  0.0     
99       22_8386_3               True   1433S_HUMAN                  0.0     

    protein_group_PEP      protein position_in_protein  uniprot_id  \
0        1.420040e-06   B2MG_HUMAN               33-40      P61769   
1        1.091970e-06    H13_HUMAN             124-131      P16402   
2        1.008520e-03   K2C1_HUMAN               30-38      P04264   
3        1.008520e-03   K2C1_HUMAN               29-37  K2C1_HUMAN   
4        3.736980e-11    sp|P04264               30-38   sp|P04264   
..                ...          ...                 ...         ...   
95       1.170320e-08  1433E_HUMAN               43-51      P62258   
96       2.411550e-11  1433T_HUMAN               42-50      P27348   
97       3.213020e-09  1433Z_HUMAN               42-50      P63104   
98       7.159880e-07  1433F_HUMAN               43-51      Q04917   
99       8.522850e-04  1433S_HUMAN               42-50      P31947   

    protein_length  protein_description  ... modifications_delta  \
0              119  Beta-2-microglob...  ...                 NaN   
1              221        Histone H1.3   ...                  0|   
2              643         contaminant   ...                 NaN   
3              643         contaminant   ...                 NaN   
4              644  SWISS-PROT|P0426...  ...                 NaN   
..             ...                  ...  ...                 ...   
95             255  14-3-3 protein e...  ...                  0|   
96             245  14-3-3 protein t...  ...                  0|   
97             245  14-3-3 protein z...  ...                  0|   
98             246  14-3-3 protein eta   ...                  0|   
99             248  14-3-3 protein s...  ...                  0|   

    best_tag_rank corrected_retention_time  unexpected_modification  database  \
0             NaN                  NaN                      NaN           NaN   
1             1.0             1914.745                      NaN             T   
2             NaN                  NaN                      NaN           NaN   
3             NaN                  NaN                      NaN           NaN   
4             NaN                  NaN                      NaN           NaN   
..            ...                  ...                      ...           ...   
95            4.0             3036.916                      NaN             T   
96            4.0             3036.916                      NaN             T   
97            4.0             3036.916                      NaN             T   
98            4.0             3036.916                      NaN             T   
99            4.0             3036.916                      NaN             T   

    psm_score  q-value    PEP             proteins   rank  
0         NaN      NaN    NaN                  NaN    NaN  
1       0.447    0.002  0.033  H13_HUMAN((124-1...  first  
2         NaN      NaN    NaN                  NaN    NaN  
3         NaN      NaN    NaN                  NaN    NaN  
4         NaN      NaN    NaN                  NaN    NaN  
..        ...      ...    ...                  ...    ...  
95      0.330  

In [96]:
tmp = proteins[proteins["unexpected_modification"].notna()]
tmp[["ionbot_match_id","unexpected_modification"]]

ionbot_match_id unexpected_modification
22            3_8327_1  [254]Delta:H(2)C...   
25            9_8303_2  [254]Delta:H(2)C...   
37           14_8590_3  [254]Delta:H(2)C...   
45           11_8617_2  [4]Carbamidometh...   
48           14_8591_1     [7]Deamidated[N]   
...                ...                  ...   
479950       11_8615_2        [34]Methyl[E]   
479954        8_8335_3  [254]Delta:H(2)C...   
479969       14_8589_2  [4]Carbamidometh...   
479970       14_8589_2  [4]Carbamidometh...   
479977        4_8602_2     [35]Oxidation[P]   

[90732 rows x 2 columns]

In [97]:
tmp = tmp.drop_duplicates(["matched_peptide","unexpected_modification"])["protein_group"].value_counts().reset_index(level=0)
tmp.columns = ["protein_group","#peptidoforms"]
tmp

protein_group  #peptidoforms
0       MYH9_HUMAN            701
1       ACTG_HUMAN            685
2       AHNK_HUMAN            619
3         H4_HUMAN            508
4       K2C1_HUMAN            410
...            ...            ...
4787   NUAK1_HUMAN              1
4788   PKRI1_HUMAN              1
4789   AMPD2_HUMAN              1
4790   DTX3L_HUMAN              1
4791   MB12A_HUMAN              1

[4792 rows x 2 columns]

In [99]:
ionbot[ionbot["proteins"]=="MYH9_HUMAN"]


Empty DataFrame
Columns: [ionbot_match_id, spectrum_title, scan, spectrum_file, precursor_mass, peptide_mass, observed_retention_time, charge, database_peptide, matched_peptide, modifications, modifications_delta, best_tag_rank, corrected_retention_time, unexpected_modification, database, psm_score, q-value, PEP, proteins, rank]
Index: []

[0 rows x 21 columns]

In [80]:
proteins.columns

Index(['ionbot_match_id', 'is_shared_peptide', 'protein_group',
       'protein_group_q-value', 'protein_group_PEP', 'protein',
       'position_in_protein', 'uniprot_id', 'protein_length',
       'protein_description', 'spectrum_title', 'scan', 'spectrum_file',
       'precursor_mass', 'peptide_mass', 'observed_retention_time', 'charge',
       'database_peptide', 'matched_peptide', 'modifications',
       'modifications_delta', 'best_tag_rank', 'corrected_retention_time',
       'unexpected_modification', 'database', 'psm_score', 'q-value', 'PEP',
       'proteins', 'rank', '#peptidoforms'],
      dtype='object')

In [87]:
print(proteins["#peptidoforms"].max())

701.0


In [88]:
cols_to_use = ["protein_group","position_in_protein","peptide_mass","matched_peptide","matched_peptide","unexpected_modification"]

proteins[proteins["#peptidoforms"]==701][cols_to_use].to_csv("dd.csv",index=False)

Prepare the result files:

The result files are written to the folder `Data/ionbot_result`:

In [35]:
cols_to_use = ['sample','matched_peptide','peptide_mass','#peptidoforms',
       'max_psm_score', 'max_all-count', 'max_all-explained',
       'max_by-intensity-pattern-correlation', 'min_rt-pred-error']

tmp = []
for sample in samples:
    print(sample)
    folder = "%s/%s/Data/ionbot_result/"%(experiment,sample)
    ionbot_first = pd.read_csv("%s/ionbot.first.csv"%folder)
    ionbot_first["rank"] = ["first"]*len(ionbot_first)
    ionbot_lower = pd.read_csv("%s/ionbot.lower.csv"%folder)
    ionbot_lower["rank"] = ["lower"]*len(ionbot_lower)
    ionbot = pd.concat([ionbot_first,ionbot_lower])
    ionbot = ionbot[(ionbot["database"]=="T")&(ionbot["q-value"]<=0.01)]
    ionbot["modifications"].fillna("-",inplace=True)
    ionbot_features = pd.read_csv("%s/ionbot.features.csv"%folder)
    ionbot = ionbot.merge(ionbot_features,on="ionbot_match_id",how="left")
    ionbot["sample"] = [sample]*len(ionbot)
    #add number of peptidoforms for each peptide
    ionbot["#peptidoforms"] = ionbot.groupby('matched_peptide')['modifications'].transform('count')
    #add max of colds for matched peptide
    cols = ["psm_score","all-count","all-explained","by-intensity-pattern-correlation"]
    for col in cols:
        ionbot["max_"+col] = ionbot.groupby('matched_peptide')[col].transform('max')    
    #add min for rt-pred-error for matched peptide
    ionbot["min_rt-pred-error"] = ionbot.groupby('matched_peptide')['rt-pred-error'].transform('min')
    ionbot = ionbot[cols_to_use]
    ionbot.drop_duplicates(["matched_peptide"],inplace=True)
    tmp.append(ionbot)
ionbot = pd.concat(tmp)

PXD000561_closed
PXD000561_full
PXD000561_nocorr_nort


In [36]:
ionbot.columns

Index(['sample', 'matched_peptide', 'peptide_mass', '#peptidoforms',
       'max_psm_score', 'max_all-count', 'max_all-explained',
       'max_by-intensity-pattern-correlation', 'min_rt-pred-error'],
      dtype='object')

In [37]:
ionbot.head(1000)

sample matched_peptide  peptide_mass  #peptidoforms  \
0     PXD000561_closed         AGAAKPR       669.392              1   
1     PXD000561_closed        RTTSSSTR       894.452              4   
2     PXD000561_closed         GAGTDEK       676.303              3   
3     PXD000561_closed         HPAENGK       751.361              2   
4     PXD000561_closed       KPEGKPDQK      1025.550              2   
...                ...             ...           ...            ...   
1210  PXD000561_closed         HSPESSR       798.362              1   
1211  PXD000561_closed       KPAAAAGAK       783.460             19   
1213  PXD000561_closed         AVEHINK       809.440              8   
1214  PXD000561_closed         RREEEMR      1004.482              4   
1215  PXD000561_closed       APRPTRPDK      1036.578              3   

      max_psm_score  max_all-count  max_all-explained  \
0             1.042             29              0.589   
1             0.846             32              0.346   
2             0.741             51              0.630   
3             0.388             42              0.588   
4             1.173             36              0.601   
...             ...            ...                ...   
1210          0.192             30              0.341   
1211          2.158             53              0.810   
1213          1.104             37              0.527   
1214          0.992             49              0.430   
1215          0.162             44              0.335   

      max_by-intensity-pattern-correlation  min_rt-pred-error  
0                   0.906                             397.597  
1                   0.880                             736.804  
2                   0.987                             548.894  
3                   0.904                            1577.966  
4                   0.857                             506.792  
...                   ...                                 ...  
1210                0.971                            1221.109  
1211                0.931                             701.461  
1213                0.981                             415.931  
1214                0.883                             120.249  
1215                0.910                             468.765  

[1000 rows x 9 columns]

In [38]:
tmp = ionbot["sample"].value_counts().reset_index(level=0)
tmp.columns = ["sample","#ids"]
fig = px.bar(tmp, y='sample', x='#ids', orientation='h')
fig.update_layout(yaxis={'categoryorder':'total ascending'})
fig.show()

In [39]:
p = {}
for sample in samples:
    p[sample] = list(ionbot[ionbot["sample"]==sample]["matched_peptide"].unique())

In [40]:
d = []
for sample1 in p:
    dd = []
    for sample2 in p:
        dd.append(len(set(p[sample1]).intersection(set(p[sample2]))))
    d.append(dd)
    
intersect = pd.DataFrame(d,columns=p,index=p)

In [41]:
intersect.style.background_gradient(cmap='Blues')

In [42]:
tmp = ionbot[ionbot["sample"]=="PXD000561_full"].drop_duplicates(["matched_peptide","modifications"])["protein_group"].value_counts().reset_index(level=0)
tmp.columns = ["protein_group","#peptidoforms"]
tmp

KeyError: Index(['modifications'], dtype='object')

The content of the result files is described [here](https://ionbot.cloud/help).

First, we load the result file that contains the first ranked matches for each MS2 spectrum:

In [ ]:
ionbot = pd.read_csv("%s/ionbot.first.csv"%result_folder)

These are the column names:

In [ ]:
for col in ionbot.columns:
    print(col)

Let's print some columns and explain the content:

In [ ]:
cols_to_use = ["ionbot_match_id","database_peptide","matched_peptide",
               "modifications","modifications_delta","unexpected_modification"]
ionbot[cols_to_use]

The column `database` is `T` if the PSM matched the target database, it is `D` otherwise.

We can see that the result file contains all matches with FDR<1%:

In [ ]:
print(ionbot["database"].value_counts())

The column `psm_score` contains the SVM (Percolator 3.0) score (i.e. the PSM score) for the matched spectra:

In [ ]:
fig = px.histogram(ionbot, x="psm_score", color="database", nbins=50)
fig.show()

Next, we load the result file that contains the lower ranked (co-eluting) matches for each MS2 spectrum and add these to the search results:

In [ ]:
ionbot["rank"] = ["first"]*len(ionbot)
tmp = pd.read_csv("%s/ionbot.lower.csv"%result_folder)
tmp["rank"] = ["lower"]*len(tmp)
ionbot = pd.concat([ionbot,tmp])

For the remainder, we remove the matches against the decoy database:

In [ ]:
ionbot = ionbot[(ionbot["database"]=="T")]

While adding the lower ranked matches we created a column `rank` that contains 'first' if the match was ranked first based on the psm_score, and 'lower' otherwise:

In [ ]:
print(ionbot["rank"].value_counts())

To reconstruct the LC-MS for matched MS2 spectra we can use the `observed_retention_time` and `precursor_mass` columns: 

In [ ]:
fig = px.scatter(ionbot, x="observed_retention_time", y="precursor_mass")
fig.update_traces(marker=dict(size=2))
fig.show()

In [ ]:
ionbot["matched_peptide"].value_counts().reset_index(level=0)

In [ ]:
tmp = ionbot["matched_peptide"].value_counts().value_counts().reset_index(level=0)
fig = px.pie(tmp, values='matched_peptide', names='index', title="#PSMs for each peptide")
fig.show()

In [ ]:
ionbot["matched_peptide"].value_counts().value_counts().plot(kind="pie")

In [ ]:
ionbot["unexpected_modification"].value_counts()

In [ ]:
ionbot["unexpected_modification"].value_counts().value_counts().plot(kind="pie")

In [ ]:
ionbot["proteins"].value_counts()

In [ ]:
features = pd.read_csv("%s/ionbot.features.csv"%result_folder)
print(features.columns)
ionbot = ionbot.merge(features,on="ionbot_match_id",how="left")

In [ ]:
ionbot.boxplot(column=["by-count","all-count"])

In [ ]:
ionbot.boxplot(column=["by-explained","all-explained"])

In [ ]:
ionbot.boxplot(column=["by-intensity-pattern-correlation"])

In [ ]:
ionbot.boxplot(column=["rt-pred-error"])

In [ ]:
fig = px.scatter(ionbot, x="observed_retention_time", y="predicted_retention_time")
fig.update_traces(marker=dict(size=2))
fig.show()

In [ ]:
fig = px.scatter(ionbot, x="corrected_retention_time", y="predicted_retention_time")
fig.update_traces(marker=dict(size=2))
fig.show()

are these outliers specific modifications?
can we show other modificatiosn (like the ones robbin presented) predicted correctly?

In [ ]:
dataset = "PXD000561"

def get_universal_link(x):
    file = '.'.join(x["spectrum_file"].split('.')[:-1])
    if str(x["modifications"]) == "nan":
        link = "http://proteomecentral.proteomexchange.org/usi/?usi=mzspec:%s:%s:scan:%i:%s/%i"%(dataset,file,x["scan"],x["matched_peptide"],x["charge"])
    else:
        tmp = x["modifications_delta"].split("|")
        seq = list(x["matched_peptide"])
        for i in range(0,len(tmp),2):
            #print("%i %i"%(len(seq),int(tmp[i])))
            #print(x["modifications"])
            pos = int(tmp[i])
            delta = tmp[i+1]
            if not delta.startswith('-'):
                delta = '%2B' + delta
            if pos == 0: #N-TERM
                seq.insert(pos,"[%s]"%delta)
            elif pos == len(seq)+1: #C-TERM
                seq.insert(pos-2,"[%s]"%delta)
            else:
                seq.insert(pos,"[%s]"%delta)
        link = "http://proteomecentral.proteomexchange.org/usi/?usi=mzspec:%s:%s:scan:%i:%s/%i"%(dataset,file,x["scan"],''.join(seq),x["charge"])
    return f'<a target="_blank" href="%s">click</a>'%link      
 

In [ ]:
ionbot["USI"] = ionbot.apply(get_universal_link,axis=1)

In [ ]:
ionbot[["ionbot_match_id","matched_peptide","modifications","modifications_delta","USI"]]